# Подготовка данных

In [1]:
import pandas as pd
import numpy as np
from sklearn import model_selection, metrics

In [2]:
# Импорт предобработанного датафрейма
df = pd.read_csv('insurance_preprocessed.csv', index_col=0)

In [3]:
# Вывод первых пяти записей из датафрейма
df.head()

age  sex     bmi  children  smoker  region      charges
0   19    0  27.900         0       1       1  16884.92400
1   18    1  33.770         1       0       2   1725.55230
2   28    1  33.000         3       0       2   4449.46200
3   33    1  22.705         0       0       3  21984.47061
4   32    1  28.880         0       0       3   3866.85520

In [4]:
# Информация о датафрейме
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1338 entries, 0 to 1337
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   age       1338 non-null   int64  
 1   sex       1338 non-null   int64  
 2   bmi       1338 non-null   float64
 3   children  1338 non-null   int64  
 4   smoker    1338 non-null   int64  
 5   region    1338 non-null   int64  
 6   charges   1338 non-null   float64
dtypes: float64(2), int64(5)
memory usage: 83.6 KB


In [5]:
# Количество неопределенных элементов
df.isnull().sum()

age         0
sex         0
bmi         0
children    0
smoker      0
region      0
charges     0
dtype: int64

In [6]:
# Разделение признаков 
y = df['charges'].values
df.pop('charges')
X = df.values

In [7]:
# Разбиение датасета на обучаемую и тестовую выборки
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=0.25)

In [8]:
# Масштабирование признаков в векторе X
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaler.fit(X_train)

X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

# Обучение моделей

## Линейная регрессия

In [9]:
# Импорт модели линейной регрессии
from sklearn.linear_model import LinearRegression

In [10]:
# https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LinearRegression.html

# Создание линейного регрессора
lin_reg = LinearRegression()

# Обучение линейного регрессора
lin_reg.fit(X_train, y_train)

LinearRegression()

### Качество модели до подбора гиперпараметров

In [11]:
# R^2 score
metrics.r2_score(y_test, lin_reg.predict(X_test))

0.762262201583743

In [12]:
# MSE score
metrics.mean_squared_error(y_test,lin_reg.predict(X_test))

36124912.52711438

In [13]:
# RMSE score
metrics.mean_squared_error(y_test, lin_reg.predict(X_test), squared=False)

6010.400363296473

In [14]:
# MAE score
metrics.mean_absolute_error(y_test, lin_reg.predict(X_test))

4135.327318857046

### Подбор гиперпараметров

In [15]:
# Текущие гиперпараметры модели
lin_reg.get_params()

{'copy_X': True, 'fit_intercept': True, 'n_jobs': None, 'normalize': False}

In [16]:
# Словарь гиперпараметров, с помощью которых будет искаться оптимальная модель
params = {
    'fit_intercept' : [False, True],
    'normalize' : [False, True]
}

In [17]:
# Поиск оптимальной модели линейной регрессии
grid_lin_reg = model_selection.GridSearchCV(lin_reg, params)

# Обучение оптимальной модели
grid_lin_reg.fit(X_train, y_train)

GridSearchCV(estimator=LinearRegression(),
             param_grid={'fit_intercept': [False, True],
                         'normalize': [False, True]})

In [18]:
# Результаты поиска гиперпараметров
grid_lin_reg.cv_results_

{'mean_fit_time': array([0.0007021 , 0.00060043, 0.00040026, 0.00100002]),
 'std_fit_time': array([0.00039781, 0.00049025, 0.00049021, 0.00063241]),
 'mean_score_time': array([0.00059829, 0.00040035, 0.00059972, 0.00039978]),
 'std_score_time': array([0.00048851, 0.00049033, 0.00048967, 0.00048963]),
 'param_fit_intercept': masked_array(data=[False, False, True, True],
              mask=[False, False, False, False],
        fill_value='?',
             dtype=object),
 'param_normalize': masked_array(data=[False, True, False, True],
              mask=[False, False, False, False],
        fill_value='?',
             dtype=object),
 'params': [{'fit_intercept': False, 'normalize': False},
  {'fit_intercept': False, 'normalize': True},
  {'fit_intercept': True, 'normalize': False},
  {'fit_intercept': True, 'normalize': True}],
 'split0_test_score': array([-0.36908908, -0.36908908,  0.75729598,  0.75729598]),
 'split1_test_score': array([-0.40169142, -0.40169142,  0.7370603 ,  0.7370603

In [19]:
# Оптимальная модель
grid_lin_reg.best_estimator_

LinearRegression()

### Качество модели после подбора гиперпараметров

In [20]:
# R^2 score
metrics.r2_score(y_test, grid_lin_reg.predict(X_test))

0.762262201583743

In [21]:
# MSE score
metrics.mean_squared_error(y_test, grid_lin_reg.predict(X_test))

36124912.52711438

In [22]:
# RMSE score
metrics.mean_squared_error(y_test, grid_lin_reg.predict(X_test), squared=False)

6010.400363296473

In [23]:
# MAE score
metrics.mean_absolute_error(y_test, grid_lin_reg.predict(X_test))

4135.327318857046

## Регрессия дерева решений

In [24]:
# Импорт модели дерева решений 
from sklearn.tree import DecisionTreeRegressor

In [25]:
# https://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeRegressor.html

# Создание модели дерева решений
tree_reg = DecisionTreeRegressor()

# Обучение модели дерева решений
tree_reg.fit(X_train, y_train)

DecisionTreeRegressor()

### Качество модели до подбора гиперпараметров

In [26]:
# R^2 score
metrics.r2_score(y_test, tree_reg.predict(X_test))

0.7178879060022492

In [27]:
# MSE score
metrics.mean_squared_error(y_test,tree_reg.predict(X_test))

42867708.822077334

In [28]:
# RMSE score
metrics.mean_squared_error(y_test, tree_reg.predict(X_test), squared=False)

6547.3436462490145

In [29]:
# MAE score
metrics.mean_absolute_error(y_test, tree_reg.predict(X_test))

3026.9333351044775

### Подбор гиперпараметров

In [30]:
# Текущие гиперпараметры модели
tree_reg.get_params()

{'ccp_alpha': 0.0,
 'criterion': 'mse',
 'max_depth': None,
 'max_features': None,
 'max_leaf_nodes': None,
 'min_impurity_decrease': 0.0,
 'min_impurity_split': None,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.0,
 'presort': 'deprecated',
 'random_state': None,
 'splitter': 'best'}

In [31]:
# Словарь гиперпараметров, с помощью которых будет искаться оптимальная модель
params = {
    'ccp_alpha' : list(np.arange(0, 1, 0.1)),
    'criterion' : ["mse", "friedman_mse", "mae", "poisson"],
    'max_depth' : list(range(5, 15)),
    'max_features' : ["auto", "log2", "sqrt"],
}

In [32]:
# Поиск оптимальной модели решающего дерева
grid_tree_reg = model_selection.GridSearchCV(tree_reg, params)

# Обучение оптимальной модели
grid_tree_reg.fit(X_train, y_train)

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

...

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 1242, in fit
    super().fit(
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\tree\_classes.py", line 336, in fit
    criterion = CRITERIA_REG[self.criterion](self.n_outputs_,
KeyError: 'poisson'

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
T

GridSearchCV(estimator=DecisionTreeRegressor(),
             param_grid={'ccp_alpha': [0.0, 0.1, 0.2, 0.30000000000000004, 0.4,
                                       0.5, 0.6000000000000001,
                                       0.7000000000000001, 0.8, 0.9],
                         'criterion': ['mse', 'friedman_mse', 'mae', 'poisson'],
                         'max_depth': [5, 6, 7, 8, 9, 10, 11, 12, 13, 14],
                         'max_features': ['auto', 'log2', 'sqrt']})

In [33]:
# Результаты поиска гиперпараметров
grid_tree_reg.cv_results_

{'mean_fit_time': array([0.0010006 , 0.00080194, 0.00060005, ..., 0.00079994, 0.        ,
        0.        ]),
 'std_fit_time': array([1.02396825e-05, 4.00973004e-04, 4.89940803e-04, ...,
        3.99976750e-04, 0.00000000e+00, 0.00000000e+00]),
 'mean_score_time': array([0.00070391, 0.00039973, 0.00039988, ..., 0.        , 0.        ,
        0.        ]),
 'std_score_time': array([0.00039772, 0.00048957, 0.00048975, ..., 0.        , 0.        ,
        0.        ]),
 'param_ccp_alpha': masked_array(data=[0.0, 0.0, 0.0, ..., 0.9, 0.9, 0.9],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_criterion': masked_array(data=['mse', 'mse', 'mse', ..., 'poisson', 'poisson',
                    'poisson'],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_max_depth': masked_array(data=[5, 5, 5, ..., 14, 14, 14],
              mask=[False,

In [34]:
# Оптимальная модель
grid_tree_reg.best_estimator_

DecisionTreeRegressor(criterion='mae', max_depth=5, max_features='auto')

### Качество модели после подбора гиперпараметров

In [35]:
# R^2 score
metrics.r2_score(y_test, grid_tree_reg.predict(X_test))

0.8516826381667184

In [36]:
# MSE score
metrics.mean_squared_error(y_test, grid_tree_reg.predict(X_test))

22537231.177258536

In [37]:
# RMSE score
metrics.mean_squared_error(y_test, grid_tree_reg.predict(X_test), squared=False)

4747.339378774024

In [38]:
# MAE score
metrics.mean_absolute_error(y_test, grid_tree_reg.predict(X_test))

1915.5925877761192

## Lasso

In [39]:
# Импорт модели линейного регрессора с регуляризатором L1
from sklearn.linear_model import Lasso

In [40]:
# https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.Lasso.html#sklearn.linear_model.Lasso

# Создание модели
lasso_reg = Lasso()

# Обучение модели
lasso_reg.fit(X_train, y_train)

Lasso()

### Качество модели до подбора гиперпараметров

In [41]:
# R^2 score
metrics.r2_score(y_test, lasso_reg.predict(X_test))

0.7622593763155345

In [42]:
# MSE score
metrics.mean_squared_error(y_test,lasso_reg.predict(X_test))

36125341.83439145

In [43]:
# RMSE score
metrics.mean_squared_error(y_test, lasso_reg.predict(X_test), squared=False)

6010.436076890882

In [44]:
# MAE score
metrics.mean_absolute_error(y_test, lasso_reg.predict(X_test))

4135.28096406428

### Подбор гиперпараметров

In [45]:
# Текущие гиперпараметры модели
lasso_reg.get_params()

{'alpha': 1.0,
 'copy_X': True,
 'fit_intercept': True,
 'max_iter': 1000,
 'normalize': False,
 'positive': False,
 'precompute': False,
 'random_state': None,
 'selection': 'cyclic',
 'tol': 0.0001,
 'warm_start': False}

In [46]:
# Словарь гиперпараметров, с помощью которых будет искаться оптимальная модель
params = {
    'alpha': list(np.arange(0.1, 1.1, 0.1)),
    'fit_intercept': [False, True],
    'normalize': [False, True],
    'positive': [False, True],
    'selection': ['сyclic', 'random'],
    'tol': [1e-4, 1e-5, 1e-6, 1e-7],
    'warm_start': [False, True]
}

In [47]:
# Поиск оптимальной модели
grid_lasso_reg = model_selection.GridSearchCV(lasso_reg, params)

# Обучение модели
grid_lasso_reg.fit(X_train, y_train)

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

...

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\vano_\anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py", line 813, in fit
    raise ValueError("selection should be either random or cyclic.")
ValueError: selection should be either random or cyclic.

  warnings.warn("Estimator fit failed. The score on this train-test"
C:\Users\vano_\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:548: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users

GridSearchCV(estimator=Lasso(),
             param_grid={'alpha': [0.1, 0.2, 0.30000000000000004, 0.4, 0.5, 0.6,
                                   0.7000000000000001, 0.8, 0.9, 1.0],
                         'fit_intercept': [False, True],
                         'normalize': [False, True], 'positive': [False, True],
                         'selection': ['сyclic', 'random'],
                         'tol': [0.0001, 1e-05, 1e-06, 1e-07],
                         'warm_start': [False, True]})

In [48]:
# Результаты поиска гиперпараметров
grid_lasso_reg.cv_results_

{'mean_fit_time': array([0.00040026, 0.00060029, 0.00040088, ..., 0.00080037, 0.00099888,
        0.00060091]),
 'std_fit_time': array([4.90214722e-04, 4.90135216e-04, 4.90972101e-04, ...,
        4.00187925e-04, 3.07032776e-06, 4.90647748e-04]),
 'mean_score_time': array([0.        , 0.        , 0.        , ..., 0.00020018, 0.        ,
        0.00039949]),
 'std_score_time': array([0.        , 0.        , 0.        , ..., 0.00040035, 0.        ,
        0.00048928]),
 'param_alpha': masked_array(data=[0.1, 0.1, 0.1, ..., 1.0, 1.0, 1.0],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_fit_intercept': masked_array(data=[False, False, False, ..., True, True, True],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_normalize': masked_array(data=[False, False, False, ..., True, True, True],
              mask=[False, False, False, ..

In [49]:
# Оптимальная модель
grid_lasso_reg.best_estimator_

Lasso(alpha=0.5, normalize=True, positive=True, selection='random')

### Качество модели после подбора гиперпараметров

In [50]:
# R^2 score
metrics.r2_score(y_test, grid_lasso_reg.predict(X_test))

0.762262380940868

In [51]:
# MSE score
metrics.mean_squared_error(y_test, grid_lasso_reg.predict(X_test))

36124885.27330581

In [52]:
# RMSE score
metrics.mean_squared_error(y_test, grid_lasso_reg.predict(X_test), squared=False)

6010.398096075318

In [53]:
# MAE score
metrics.mean_absolute_error(y_test, grid_lasso_reg.predict(X_test))

4133.802192954233

## Гребневая регрессия

In [54]:
# Импорт модели линейного регрессора с регуляризатором L2
from sklearn.linear_model import Ridge

In [55]:
# https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.Ridge.html#sklearn.linear_model.Ridge

# Создание модели
ridge_reg = Ridge()

# Обучение модели
ridge_reg.fit(X_train, y_train)

Ridge()

### Качество модели до подбора гиперпараметров

In [56]:
# R^2 score
metrics.r2_score(y_test, ridge_reg.predict(X_test))

0.7622268455122782

In [57]:
# MSE score
metrics.mean_squared_error(y_test, ridge_reg.predict(X_test))

36130284.97944413

In [58]:
# RMSE score
metrics.mean_squared_error(y_test, ridge_reg.predict(X_test), squared=False)

6010.8472763366835

In [59]:
# MAE score
metrics.mean_absolute_error(y_test, ridge_reg.predict(X_test))

4136.770699230455

### Подбор гиперпараметров

In [60]:
# Текущие гиперпараметры модели
ridge_reg.get_params()

{'alpha': 1.0,
 'copy_X': True,
 'fit_intercept': True,
 'max_iter': None,
 'normalize': False,
 'random_state': None,
 'solver': 'auto',
 'tol': 0.001}

In [61]:
# Словарь гиперпараметров, с помощью которых будет искаться оптимальная модель
params = {
    'alpha' : list(np.arange(0.1, 1.1, 0.1)),
    'fit_intercept': [True, False],
    'max_iter' : [1000, 1100, 1200, 1250, 1300],
    'normalize': [False, True],
    'solver': ['auto', 'svd', 'cholesky', 'lsqr', 'sparse_cg', 'sag', 'saga'],
    'tol': [1e-4, 1e-5, 1e-6, 1e-7]
}

In [62]:
# Поиск оптимальной модели
grid_ridge_reg = model_selection.GridSearchCV(ridge_reg, params)

# Обучение оптимальной модели
grid_ridge_reg.fit(X_train, y_train)

GridSearchCV(estimator=Ridge(),
             param_grid={'alpha': [0.1, 0.2, 0.30000000000000004, 0.4, 0.5, 0.6,
                                   0.7000000000000001, 0.8, 0.9, 1.0],
                         'fit_intercept': [True, False],
                         'max_iter': [1000, 1100, 1200, 1250, 1300],
                         'normalize': [False, True],
                         'solver': ['auto', 'svd', 'cholesky', 'lsqr',
                                    'sparse_cg', 'sag', 'saga'],
                         'tol': [0.0001, 1e-05, 1e-06, 1e-07]})

In [63]:
# Результаты подбора гиперпараметров
grid_ridge_reg.cv_results_

{'mean_fit_time': array([0.0011065 , 0.00079975, 0.00040021, ..., 0.00219994, 0.00239859,
        0.0027998 ]),
 'std_fit_time': array([0.00021303, 0.00039988, 0.00049016, ..., 0.00040017, 0.00049088,
        0.00040057]),
 'mean_score_time': array([0.00035887, 0.0001996 , 0.00059967, ..., 0.0003994 , 0.00040035,
        0.00060024]),
 'std_score_time': array([0.00044421, 0.00039921, 0.00048963, ..., 0.00048916, 0.00049033,
        0.0004901 ]),
 'param_alpha': masked_array(data=[0.1, 0.1, 0.1, ..., 1.0, 1.0, 1.0],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_fit_intercept': masked_array(data=[True, True, True, ..., False, False, False],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_max_iter': masked_array(data=[1000, 1000, 1000, ..., 1300, 1300, 1300],
              mask=[False, False, False, ..., False, False, False],
   

In [64]:
# Оптимальная модель
grid_ridge_reg.best_estimator_

Ridge(alpha=0.9, max_iter=1200, solver='sag', tol=0.0001)

### Качество модели после подбора гиперпараметров

In [65]:
# R^2 score
metrics.r2_score(y_test, grid_ridge_reg.predict(X_test))

0.7622279000313823

In [66]:
# MSE score
metrics.mean_squared_error(y_test, grid_ridge_reg.predict(X_test))

36130124.74236509

In [67]:
# RMSE score
metrics.mean_squared_error(y_test, grid_ridge_reg.predict(X_test), squared=False)

6010.833947329196

In [68]:
# MAE score
metrics.mean_absolute_error(y_test, grid_ridge_reg.predict(X_test))

4136.634794411979

## Elastic Net регрессия

In [69]:
# Импорт модели
from sklearn.linear_model import ElasticNet

In [70]:
# https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.ElasticNet.html#sklearn.linear_model.ElasticNet

# Создание модели
el_net_reg = ElasticNet()

# Обучение модели
el_net_reg.fit(X_train, y_train)

ElasticNet()

### Качество модели до подбора гиперпараметров

In [71]:
# R^2 score
metrics.r2_score(y_test, el_net_reg.predict(X_test))

0.6695026398928572

In [72]:
# MSE score
metrics.mean_squared_error(y_test, el_net_reg.predict(X_test))

50219983.12362739

In [73]:
# RMSE score
metrics.mean_squared_error(y_test, el_net_reg.predict(X_test), squared=False)

7086.605895887494

In [74]:
# MAE score
metrics.mean_absolute_error(y_test, el_net_reg.predict(X_test))

5130.443218120919

### Подбор гиперпараметров

In [75]:
# Текущие гиперпараметры модели
el_net_reg.get_params()

{'alpha': 1.0,
 'copy_X': True,
 'fit_intercept': True,
 'l1_ratio': 0.5,
 'max_iter': 1000,
 'normalize': False,
 'positive': False,
 'precompute': False,
 'random_state': None,
 'selection': 'cyclic',
 'tol': 0.0001,
 'warm_start': False}

In [76]:
# Словарь гиперпараметров, с помощью которых будет искаться оптимальная модель
params = {
    'alpha' : list(np.arange(0.1, 1.1, 0.1)),
    'fit_intercept': [False, True],
    'max_iter': [1000, 1100, 1200],
    'normalize': [False, True],
    'positive': [False, True],
    'selection': ['cyclic', 'random'],
    'tol': [1e-4, 1e-5, 1e-6, 1e-7],
    'warm_start': [False, True]
}

In [77]:
# Поиск оптимальной модели
grid_el_net_reg = model_selection.GridSearchCV(el_net_reg, params)

# Обучение оптимальной модели
grid_el_net_reg.fit(X_train, y_train)

GridSearchCV(estimator=ElasticNet(),
             param_grid={'alpha': [0.1, 0.2, 0.30000000000000004, 0.4, 0.5, 0.6,
                                   0.7000000000000001, 0.8, 0.9, 1.0],
                         'fit_intercept': [False, True],
                         'max_iter': [1000, 1100, 1200],
                         'normalize': [False, True], 'positive': [False, True],
                         'selection': ['cyclic', 'random'],
                         'tol': [0.0001, 1e-05, 1e-06, 1e-07],
                         'warm_start': [False, True]})

In [78]:
# Результаты подбора гиперпараметров
grid_el_net_reg.cv_results_

{'mean_fit_time': array([0.00096207, 0.00080094, 0.00040011, ..., 0.00060024, 0.00079989,
        0.00080004]),
 'std_fit_time': array([0.00051597, 0.00040047, 0.00049004, ..., 0.0004901 , 0.00039995,
        0.00040002]),
 'mean_score_time': array([0.00030465, 0.0004003 , 0.00040321, ..., 0.00040002, 0.00019999,
        0.00040045]),
 'std_score_time': array([0.00040247, 0.00049027, 0.00049385, ..., 0.00048992, 0.00039997,
        0.00049045]),
 'param_alpha': masked_array(data=[0.1, 0.1, 0.1, ..., 1.0, 1.0, 1.0],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_fit_intercept': masked_array(data=[False, False, False, ..., True, True, True],
              mask=[False, False, False, ..., False, False, False],
        fill_value='?',
             dtype=object),
 'param_max_iter': masked_array(data=[1000, 1000, 1000, ..., 1200, 1200, 1200],
              mask=[False, False, False, ..., False, False, False],
   

In [79]:
# Оптимальная модель
grid_el_net_reg.best_estimator_

ElasticNet(alpha=0.1, positive=True, selection='random')

### Качество модели после подбора гиперпараметров

In [80]:
# R^2 score
metrics.r2_score(y_test, grid_el_net_reg.predict(X_test))

0.7589417383043422

In [81]:
# MSE score
metrics.mean_squared_error(y_test, grid_el_net_reg.predict(X_test))

36629466.05758759

In [82]:
# RMSE score
metrics.mean_squared_error(y_test, grid_el_net_reg.predict(X_test), squared=False)

6052.228189484232

In [83]:
# MAE score
metrics.mean_absolute_error(y_test, grid_el_net_reg.predict(X_test))

4226.184713026157